In [2]:
import pandas as pd
import scipy.io as sio
from scipy import signal, stats
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re

upRiverDF = pd.read_csv('upriver_2013_2014_processed.csv', parse_dates = ['DN'])
upRiverDF['dayDN'] = upRiverDF['DN'].dt.floor('D')
upRiverDF["surfaceRiver"] = np.nan
upRiverDF["bottomRiver"] = np.nan

dayDN = upRiverDF['dayDN'].drop_duplicates().to_list()
for dateMark in dayDN:
    if upRiverDF.loc[(upRiverDF['dayDN'] == dateMark) & (upRiverDF["SurfaceSalCorrected"] < 0.25)].shape[0] > 0:
        # since we have values lower than 0.25 salinity, we simply need to average those respective temperature values to find the river temperature 
        dailyRiverTemperatureSurface = np.nanmean(upRiverDF.loc[(upRiverDF['dayDN'] == dateMark) & (upRiverDF["SurfaceSalCorrected"] < 0.25)]["SurfaceTemp"])
        dailyRiverTemperatureBottom = np.nanmean(upRiverDF.loc[(upRiverDF['dayDN'] == dateMark) & (upRiverDF["BottomSalCorrected"] < 0.25)]["BottomTemp"])
    else:
        # we need to plot all daily values in T vs S plots, then creating linear regression plots, to find the y-intercept for each, which gives us the average daily river temperature
        # r is the Pearson Correlation Coefficient, if linear regression is bad we need to get the appropriate temperature value for that day's low tide
        (slopeSurface, interceptSurface, rSurface, p, std_err) = stats.linregress(upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["SurfaceSalCorrected"].ffill().bfill().to_numpy(), upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["SurfaceTemp"].ffill().bfill().to_numpy(), alternative = "less")
        if abs(rSurface) < 0.2:
            dailyRiverTemperatureSurface = upRiverDF.loc[upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomPressure"].idxmin()]['SurfaceTemp']
        else:
            dailyRiverTemperatureSurface = interceptSurface
        (slopeBottom, interceptBottom, rBottom, p, std_err) = stats.linregress(upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomSalCorrected"].ffill().bfill().to_numpy(), upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomTemp"].ffill().bfill().to_numpy(), alternative = "less")
        if abs(rBottom) < 0.2:
            dailyRiverTemperatureBottom = upRiverDF.loc[upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomPressure"].idxmin()]['BottomTemp']
        else:
            dailyRiverTemperatureBottom = interceptBottom
        #print(dateMark, rSurface, rBottom)
        #creating T vs S plots for each day where salinity doesn't get to 0.25
        salinityAxisSurface = [0]
        salinityAxisBottom = [0]
        linearRegressionPlot = [interceptSurface]
        linearRegressionPlotBottom = [interceptBottom]
        for surfaceSal in upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["SurfaceSalCorrected"]:
            linearRegressionPlot.append(surfaceSal * slopeSurface + interceptSurface)
            salinityAxisSurface.append(surfaceSal)
        for bottomSal in upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomSalCorrected"]:
            linearRegressionPlotBottom.append(bottomSal * slopeBottom + interceptBottom)
            salinityAxisBottom.append(bottomSal)

        '''
        plt = px.scatter(x = upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["SurfaceSalCorrected"], y = [upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["SurfaceTemp"]])
        plt.add_scattergl(x= salinityAxisSurface, y = linearRegressionPlot, line={'color': 'red'})
        plt2 = px.scatter(x = upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomSalCorrected"], y = [upRiverDF.loc[upRiverDF['dayDN'] == dateMark]["BottomTemp"]])
        plt2.add_scattergl(x= salinityAxisBottom, y = linearRegressionPlotBottom, line={'color': 'purple'})
        plt.show()
        plt2.show()
        #input("press enter")
        '''

    upRiverDF.loc[upRiverDF['dayDN'] == dateMark, "surfaceRiver"] = dailyRiverTemperatureSurface
    upRiverDF.loc[upRiverDF['dayDN'] == dateMark, "bottomRiver"] = dailyRiverTemperatureBottom

upRiverDF['EstimatedTemp'] = (upRiverDF["bottomRiver"].ffill().bfill() + upRiverDF["surfaceRiver"].ffill().bfill())/2.0
smoothedUpRiverDF = pd.read_csv('river_temperature_interpol13_14.csv', parse_dates = ['DN'])
upRiverDF.to_csv('river_temperature13_14.csv', index=False)
tempFigLabels = ['surfaceRiver', 'bottomRiver']
tempfig = px.line(x = upRiverDF['dayDN'], y = [upRiverDF["surfaceRiver"], upRiverDF["bottomRiver"]] , color_discrete_sequence= ["cyan", "black"], title = "River Temperature")
tempfig.update_traces(patch={"line": {"dash": "dot"}})
tempfig.add_scattergl(x= upRiverDF['DN'], y = smoothedUpRiverDF["EstimatedTemp"], line={'color': 'green', 'width' : 2}, name = "River Temperature")

for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]
tempfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C)", legend_title="Locations")
tempfig.update_layout(title=dict(text= "River Temperature for 2013-2014", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp('2013-10-28'),pd.Timestamp('2014-03-15')])
tempfig.show()



C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32004\1856093871.py:21: RuntimeWarning:

Mean of empty slice

C:\Users\nvleb\AppData\Local\Temp\ipykernel_32